In [1]:
import numpy as np
import pandas as pd
import copy

import torch
from torch.utils.data import TensorDataset, DataLoader
from sklearn.preprocessing import MinMaxScaler

from data import fetch_dataset
from util import move_sliding_window, num_params

from model import LSTMModel
from algorithm import fedavg,fedlbs

pd.set_option('display.max_columns', None)
pd.set_option('display.max_columns', None)
np.set_printoptions(suppress=True, floatmode='fixed')

In [2]:
if torch.cuda.is_available():
    device = torch.device("cuda")
    print('running on gpu')
else:
    device = torch.device("cpu")

running on gpu


# Parameters

In [3]:
window_size = 90 # Define window_size period and split inputs/labels\
batch_size = 1024
label_col_index = 0

# seq_len = 90  # (timestamps)
hidden_dim = 50
n_layers = 2
lr = 0.0001
output_dim = 1

#fed train params
num_local_epochs = 1
max_rounds = 100 #nb of total rounds for training


# Data Preperation

In [4]:
dataframes = fetch_dataset("./heterog")

Floor0
Floor1
Floor10
Floor11
Floor12
Floor13
Floor14
Floor15
Floor16
Floor17
Floor18
Floor19
Floor2
Floor20
Floor21
Floor22
Floor23
Floor24
Floor25
Floor26
Floor27
Floor28
Floor29
Floor3
Floor30
Floor31
Floor32
Floor33
Floor34
Floor35
Floor36
Floor37
Floor38
Floor39
Floor4
Floor40
Floor41
Floor42
Floor43
Floor44
Floor45
Floor46
Floor47
Floor48
Floor49
Floor5
Floor50
Floor51
Floor52
Floor53
Floor54
Floor55
Floor56
Floor57
Floor58
Floor59
Floor6
Floor60
Floor61
Floor62
Floor63
Floor64
Floor65
Floor66
Floor67
Floor68
Floor69
Floor7
Floor70
Floor71
Floor72
Floor73
Floor74
Floor75
Floor76
Floor77
Floor78
Floor79
Floor8
Floor80
Floor81
Floor82
Floor83
Floor84
Floor85
Floor86
Floor87
Floor88
Floor89
Floor9


In [5]:
# n_clients = len(dataframes)

In [6]:
for _, df in dataframes.items():
    print(df.columns)
    print(df.shape)
    input_dim=df.shape[1]

Index(['total_demand', 'AC', 'Light', 'Plug', 'Year', 'Month', 'Day', 'Hour',
       'Minute'],
      dtype='object')
(68183, 9)
Index(['total_demand', 'AC', 'Light', 'Plug', 'Year', 'Month', 'Day', 'Hour',
       'Minute'],
      dtype='object')
(58618, 9)
Index(['total_demand', 'AC', 'Light', 'Plug', 'Year', 'Month', 'Day', 'Hour',
       'Minute'],
      dtype='object')
(61943, 9)
Index(['total_demand', 'AC', 'Light', 'Plug', 'Year', 'Month', 'Day', 'Hour',
       'Minute'],
      dtype='object')
(50086, 9)


# LSTM model

In [8]:
lstm = LSTMModel(input_dim, hidden_dim, output_dim, n_layers)
model_type = 'LSTM'
print(lstm)
print(num_params(lstm))

LSTMModel(
  (lstm): LSTM(9, 50, num_layers=2, batch_first=True)
  (fc): Linear(in_features=50, out_features=1, bias=True)
  (tanh): Tanh()
)
32651


# FedLbs

# Build the training set

## 10

In [5]:
n_clients=10

In [7]:
train_loader = []
test_loader = []
label_scalers = []
i=0
for _, df in dataframes.items():
    if i==n_clients:
        break
    inputs_cols_indices = range(0, df.shape[1])  # use (total_demand,Year,Month,Day,Hour,Minute) columns as features
    #move the window
    inputs, labels = move_sliding_window(
        df.values,
        window_size,
        inputs_cols_indices=inputs_cols_indices,
        label_col_index=label_col_index
    )

    # Normalize the input data columns
    sc = MinMaxScaler()
    # Obtaining the scaler for the labels(usage data) so that output can be re-scaled to actual value during evaluation
    label_sc = MinMaxScaler()

    # Split data into train/test portions and combining all data into a single array
    test_portion = int(0.2 * len(inputs))

    train_x = sc.fit_transform(inputs[:-test_portion].reshape(-1, window_size * df.shape[1]))
    train_x = train_x.reshape(-1, window_size, df.shape[1])
    train_y = label_sc.fit_transform(labels[:-test_portion])

    test_x = sc.transform(inputs[-test_portion:].reshape(-1, window_size * df.shape[1]))
    test_x = test_x.reshape(-1, window_size, df.shape[1])
    test_y = label_sc.transform(labels[-test_portion:])

    # test_x.append(testx)
    # test_y.append(testy)
    label_scalers.append(label_sc)

    # pytorch data loaders
    train_data = TensorDataset(torch.from_numpy(train_x).to('cpu'), torch.from_numpy(train_y).to('cpu'))
    train_loader.append(DataLoader(train_data, batch_size=batch_size, drop_last=True))# Drop the last incomplete batch
    test_data = TensorDataset(torch.from_numpy(test_x).to('cpu'), torch.from_numpy(test_y).to('cpu'))
    test_loader.append(DataLoader(test_data, batch_size=batch_size))# Drop the last incomplete batch

    # release some memory
    del train_x, train_y
    i=i+1


(68093, 90, 9) (68093, 1)
(58528, 90, 9) (58528, 1)
(46750, 90, 9) (46750, 1)
(65300, 90, 9) (65300, 1)
(57086, 90, 9) (57086, 1)
(51617, 90, 9) (51617, 1)
(47363, 90, 9) (47363, 1)
(68901, 90, 9) (68901, 1)
(67168, 90, 9) (67168, 1)
(69578, 90, 9) (69578, 1)


In [10]:
%%time
S = 3
lstm_K5_lbs = copy.deepcopy(lstm)
outputs_lbs, targets_lbs, loss_lbs, smape_lbs, mae_lbs, rmse_lbs = fedlbs(
    global_model = lstm_K5_lbs,
    client_train_loader = train_loader,
    test_loader = test_loader,
    label_sc = label_scalers,
    n_clients = n_clients,
    num_clients_per_round = n_clients,
    batch_size = batch_size,
    num_local_epochs = num_local_epochs,
    lr = lr,
    max_rounds = max_rounds,
    model_type = model_type,
    device = device,
    S=S
)


starting average round 0
clients:  [0 1 2 3 4 5 6 7 8 9]
round 0, starting client 1/10, id: 0
Epoch [1/1], Train Loss: 0.10940780982656297
round 0, starting client 2/10, id: 1
Epoch [1/1], Train Loss: 0.09746628229816756
round 0, starting client 3/10, id: 2
Epoch [1/1], Train Loss: 0.08357943894548549
round 0, starting client 4/10, id: 3
Epoch [1/1], Train Loss: 0.08585405751478438
round 0, starting client 5/10, id: 4
Epoch [1/1], Train Loss: 0.10313151226463643
round 0, starting client 6/10, id: 5
Epoch [1/1], Train Loss: 0.09223806727677587
round 0, starting client 7/10, id: 6
Epoch [1/1], Train Loss: 0.11234541428652971
round 0, starting client 8/10, id: 7
Epoch [1/1], Train Loss: 0.09395022310738291
round 0, starting client 9/10, id: 8
Epoch [1/1], Train Loss: 0.09307089619911632
round 0, starting client 10/10, id: 9
Epoch [1/1], Train Loss: 0.08281595097354576
calc smape: 66.54247641509059%
MAE: 11.7328522083085
RMSE: 22.136402070543383
Average Loss:  0.07641688390957917

startin

In [11]:
np.save(f'metrics/fedlbs_outputs_C{n_clients}.npy', np.array(outputs_lbs, dtype=object))
np.save(f'metrics/fedlbs_targets_C{n_clients}.npy', np.array(targets_lbs, dtype=object))
np.save(f'metrics/fedlbs_loss_C{n_clients}.npy', loss_lbs)
np.save(f'metrics/fedlbs_smape_C{n_clients}.npy', smape_lbs)
np.save(f'metrics/fedlbs_mae_C{n_clients}.npy', mae_lbs)
np.save(f'metrics/fedlbs_rmse_C{n_clients}.npy', rmse_lbs)

## 20

In [12]:
n_clients=20

In [13]:
train_loader = []
test_loader = []
label_scalers = []
i=0
for _, df in dataframes.items():
    if i==n_clients:
        break
    inputs_cols_indices = range(0, df.shape[1])  # use (total_demand,Year,Month,Day,Hour,Minute) columns as features
    #move the window
    inputs, labels = move_sliding_window(
        df.values,
        window_size,
        inputs_cols_indices=inputs_cols_indices,
        label_col_index=label_col_index
    )

    # Normalize the input data columns
    sc = MinMaxScaler()
    # Obtaining the scaler for the labels(usage data) so that output can be re-scaled to actual value during evaluation
    label_sc = MinMaxScaler()

    # Split data into train/test portions and combining all data into a single array
    test_portion = int(0.2 * len(inputs))

    train_x = sc.fit_transform(inputs[:-test_portion].reshape(-1, window_size * df.shape[1]))
    train_x = train_x.reshape(-1, window_size, df.shape[1])
    train_y = label_sc.fit_transform(labels[:-test_portion])

    test_x = sc.transform(inputs[-test_portion:].reshape(-1, window_size * df.shape[1]))
    test_x = test_x.reshape(-1, window_size, df.shape[1])
    test_y = label_sc.transform(labels[-test_portion:])

    # test_x.append(testx)
    # test_y.append(testy)
    label_scalers.append(label_sc)

    # pytorch data loaders
    train_data = TensorDataset(torch.from_numpy(train_x).to('cpu'), torch.from_numpy(train_y).to('cpu'))
    train_loader.append(DataLoader(train_data, batch_size=batch_size, drop_last=True))# Drop the last incomplete batch
    test_data = TensorDataset(torch.from_numpy(test_x).to('cpu'), torch.from_numpy(test_y).to('cpu'))
    test_loader.append(DataLoader(test_data, batch_size=batch_size))# Drop the last incomplete batch

    # release some memory
    del train_x, train_y
    i=i+1


(68093, 90, 9) (68093, 1)
(58528, 90, 9) (58528, 1)
(46750, 90, 9) (46750, 1)
(65300, 90, 9) (65300, 1)
(57086, 90, 9) (57086, 1)
(51617, 90, 9) (51617, 1)
(47363, 90, 9) (47363, 1)
(68901, 90, 9) (68901, 1)
(67168, 90, 9) (67168, 1)
(69578, 90, 9) (69578, 1)
(62003, 90, 9) (62003, 1)
(49050, 90, 9) (49050, 1)
(61853, 90, 9) (61853, 1)
(69521, 90, 9) (69521, 1)
(67302, 90, 9) (67302, 1)
(72217, 90, 9) (72217, 1)
(46055, 90, 9) (46055, 1)
(57157, 90, 9) (57157, 1)
(64807, 90, 9) (64807, 1)
(66845, 90, 9) (66845, 1)


In [14]:
%%time
S = 3
lstm_K5_lbs = copy.deepcopy(lstm)
outputs_lbs, targets_lbs, loss_lbs, smape_lbs, mae_lbs, rmse_lbs = fedlbs(
    global_model = lstm_K5_lbs,
    client_train_loader = train_loader,
    test_loader = test_loader,
    label_sc = label_scalers,
    n_clients = n_clients,
    num_clients_per_round = n_clients,
    batch_size = batch_size,
    num_local_epochs = num_local_epochs,
    lr = lr,
    max_rounds = max_rounds,
    model_type = model_type,
    device = device,
    S=S
)


starting average round 0
clients:  [ 0  1  2  3  4  5  6  7  8  9 10 11 12 13 14 15 16 17 18 19]
round 0, starting client 1/20, id: 0
Epoch [1/1], Train Loss: 0.10940780982656297
round 0, starting client 2/20, id: 1
Epoch [1/1], Train Loss: 0.09746628229816756
round 0, starting client 3/20, id: 2
Epoch [1/1], Train Loss: 0.08357943894548549
round 0, starting client 4/20, id: 3
Epoch [1/1], Train Loss: 0.08585405751478438
round 0, starting client 5/20, id: 4
Epoch [1/1], Train Loss: 0.10313151226463643
round 0, starting client 6/20, id: 5
Epoch [1/1], Train Loss: 0.09223806727677587
round 0, starting client 7/20, id: 6
Epoch [1/1], Train Loss: 0.11234541428652971
round 0, starting client 8/20, id: 7
Epoch [1/1], Train Loss: 0.09395022310738291
round 0, starting client 9/20, id: 8
Epoch [1/1], Train Loss: 0.09307089619911632
round 0, starting client 10/20, id: 9
Epoch [1/1], Train Loss: 0.08281595097354576
round 0, starting client 11/20, id: 10
Epoch [1/1], Train Loss: 0.109625788327927

In [15]:
np.save(f'metrics/fedlbs_outputs_C{n_clients}.npy', np.array(outputs_lbs, dtype=object))
np.save(f'metrics/fedlbs_targets_C{n_clients}.npy', np.array(targets_lbs, dtype=object))
np.save(f'metrics/fedlbs_loss_C{n_clients}.npy', loss_lbs)
np.save(f'metrics/fedlbs_smape_C{n_clients}.npy', smape_lbs)
np.save(f'metrics/fedlbs_mae_C{n_clients}.npy', mae_lbs)
np.save(f'metrics/fedlbs_rmse_C{n_clients}.npy', rmse_lbs)

## 30

In [16]:
n_clients=30

In [17]:
train_loader = []
test_loader = []
label_scalers = []
i=0
for _, df in dataframes.items():
    if i==n_clients:
        break
    inputs_cols_indices = range(0, df.shape[1])  # use (total_demand,Year,Month,Day,Hour,Minute) columns as features
    #move the window
    inputs, labels = move_sliding_window(
        df.values,
        window_size,
        inputs_cols_indices=inputs_cols_indices,
        label_col_index=label_col_index
    )

    # Normalize the input data columns
    sc = MinMaxScaler()
    # Obtaining the scaler for the labels(usage data) so that output can be re-scaled to actual value during evaluation
    label_sc = MinMaxScaler()

    # Split data into train/test portions and combining all data into a single array
    test_portion = int(0.2 * len(inputs))

    train_x = sc.fit_transform(inputs[:-test_portion].reshape(-1, window_size * df.shape[1]))
    train_x = train_x.reshape(-1, window_size, df.shape[1])
    train_y = label_sc.fit_transform(labels[:-test_portion])

    test_x = sc.transform(inputs[-test_portion:].reshape(-1, window_size * df.shape[1]))
    test_x = test_x.reshape(-1, window_size, df.shape[1])
    test_y = label_sc.transform(labels[-test_portion:])

    # test_x.append(testx)
    # test_y.append(testy)
    label_scalers.append(label_sc)

    # pytorch data loaders
    train_data = TensorDataset(torch.from_numpy(train_x).to('cpu'), torch.from_numpy(train_y).to('cpu'))
    train_loader.append(DataLoader(train_data, batch_size=batch_size, drop_last=True))# Drop the last incomplete batch
    test_data = TensorDataset(torch.from_numpy(test_x).to('cpu'), torch.from_numpy(test_y).to('cpu'))
    test_loader.append(DataLoader(test_data, batch_size=batch_size))# Drop the last incomplete batch

    # release some memory
    del train_x, train_y
    i=i+1


(68093, 90, 9) (68093, 1)
(58528, 90, 9) (58528, 1)
(46750, 90, 9) (46750, 1)
(65300, 90, 9) (65300, 1)
(57086, 90, 9) (57086, 1)
(51617, 90, 9) (51617, 1)
(47363, 90, 9) (47363, 1)
(68901, 90, 9) (68901, 1)
(67168, 90, 9) (67168, 1)
(69578, 90, 9) (69578, 1)
(62003, 90, 9) (62003, 1)
(49050, 90, 9) (49050, 1)
(61853, 90, 9) (61853, 1)
(69521, 90, 9) (69521, 1)
(67302, 90, 9) (67302, 1)
(72217, 90, 9) (72217, 1)
(46055, 90, 9) (46055, 1)
(57157, 90, 9) (57157, 1)
(64807, 90, 9) (64807, 1)
(66845, 90, 9) (66845, 1)
(61800, 90, 9) (61800, 1)
(55024, 90, 9) (55024, 1)
(65910, 90, 9) (65910, 1)
(49996, 90, 9) (49996, 1)
(63049, 90, 9) (63049, 1)
(64836, 90, 9) (64836, 1)
(64007, 90, 9) (64007, 1)
(69858, 90, 9) (69858, 1)
(56491, 90, 9) (56491, 1)
(65359, 90, 9) (65359, 1)


In [18]:
%%time
S = 3
lstm_K5_lbs = copy.deepcopy(lstm)
outputs_lbs, targets_lbs, loss_lbs, smape_lbs, mae_lbs, rmse_lbs = fedlbs(
    global_model = lstm_K5_lbs,
    client_train_loader = train_loader,
    test_loader = test_loader,
    label_sc = label_scalers,
    n_clients = n_clients,
    num_clients_per_round = n_clients,
    batch_size = batch_size,
    num_local_epochs = num_local_epochs,
    lr = lr,
    max_rounds = max_rounds,
    model_type = model_type,
    device = device,
    S=S
)


starting average round 0
clients:  [ 0  1  2  3  4  5  6  7  8  9 10 11 12 13 14 15 16 17 18 19 20 21 22 23
 24 25 26 27 28 29]
round 0, starting client 1/30, id: 0
Epoch [1/1], Train Loss: 0.10940780982656297
round 0, starting client 2/30, id: 1
Epoch [1/1], Train Loss: 0.09746628229816756
round 0, starting client 3/30, id: 2
Epoch [1/1], Train Loss: 0.08357943894548549
round 0, starting client 4/30, id: 3
Epoch [1/1], Train Loss: 0.08585405751478438
round 0, starting client 5/30, id: 4
Epoch [1/1], Train Loss: 0.10313151226463643
round 0, starting client 6/30, id: 5
Epoch [1/1], Train Loss: 0.09223806727677587
round 0, starting client 7/30, id: 6
Epoch [1/1], Train Loss: 0.11234541428652971
round 0, starting client 8/30, id: 7
Epoch [1/1], Train Loss: 0.09395022310738291
round 0, starting client 9/30, id: 8
Epoch [1/1], Train Loss: 0.09307089619911632
round 0, starting client 10/30, id: 9
Epoch [1/1], Train Loss: 0.08281595097354576
round 0, starting client 11/30, id: 10
Epoch [1/1]

In [19]:
np.save(f'metrics/fedlbs_outputs_C{n_clients}.npy', np.array(outputs_lbs, dtype=object))
np.save(f'metrics/fedlbs_targets_C{n_clients}.npy', np.array(targets_lbs, dtype=object))
np.save(f'metrics/fedlbs_loss_C{n_clients}.npy', loss_lbs)
np.save(f'metrics/fedlbs_smape_C{n_clients}.npy', smape_lbs)
np.save(f'metrics/fedlbs_mae_C{n_clients}.npy', mae_lbs)
np.save(f'metrics/fedlbs_rmse_C{n_clients}.npy', rmse_lbs)

## 40

In [20]:
n_clients=40

In [21]:
train_loader = []
test_loader = []
label_scalers = []
i=0
for _, df in dataframes.items():
    if i==n_clients:
        break
    inputs_cols_indices = range(0, df.shape[1])  # use (total_demand,Year,Month,Day,Hour,Minute) columns as features
    #move the window
    inputs, labels = move_sliding_window(
        df.values,
        window_size,
        inputs_cols_indices=inputs_cols_indices,
        label_col_index=label_col_index
    )

    # Normalize the input data columns
    sc = MinMaxScaler()
    # Obtaining the scaler for the labels(usage data) so that output can be re-scaled to actual value during evaluation
    label_sc = MinMaxScaler()

    # Split data into train/test portions and combining all data into a single array
    test_portion = int(0.2 * len(inputs))

    train_x = sc.fit_transform(inputs[:-test_portion].reshape(-1, window_size * df.shape[1]))
    train_x = train_x.reshape(-1, window_size, df.shape[1])
    train_y = label_sc.fit_transform(labels[:-test_portion])

    test_x = sc.transform(inputs[-test_portion:].reshape(-1, window_size * df.shape[1]))
    test_x = test_x.reshape(-1, window_size, df.shape[1])
    test_y = label_sc.transform(labels[-test_portion:])

    # test_x.append(testx)
    # test_y.append(testy)
    label_scalers.append(label_sc)

    # pytorch data loaders
    train_data = TensorDataset(torch.from_numpy(train_x).to('cpu'), torch.from_numpy(train_y).to('cpu'))
    train_loader.append(DataLoader(train_data, batch_size=batch_size, drop_last=True))# Drop the last incomplete batch
    test_data = TensorDataset(torch.from_numpy(test_x).to('cpu'), torch.from_numpy(test_y).to('cpu'))
    test_loader.append(DataLoader(test_data, batch_size=batch_size))# Drop the last incomplete batch

    # release some memory
    del train_x, train_y
    i=i+1


(68093, 90, 9) (68093, 1)
(58528, 90, 9) (58528, 1)
(46750, 90, 9) (46750, 1)
(65300, 90, 9) (65300, 1)
(57086, 90, 9) (57086, 1)
(51617, 90, 9) (51617, 1)
(47363, 90, 9) (47363, 1)
(68901, 90, 9) (68901, 1)
(67168, 90, 9) (67168, 1)
(69578, 90, 9) (69578, 1)
(62003, 90, 9) (62003, 1)
(49050, 90, 9) (49050, 1)
(61853, 90, 9) (61853, 1)
(69521, 90, 9) (69521, 1)
(67302, 90, 9) (67302, 1)
(72217, 90, 9) (72217, 1)
(46055, 90, 9) (46055, 1)
(57157, 90, 9) (57157, 1)
(64807, 90, 9) (64807, 1)
(66845, 90, 9) (66845, 1)
(61800, 90, 9) (61800, 1)
(55024, 90, 9) (55024, 1)
(65910, 90, 9) (65910, 1)
(49996, 90, 9) (49996, 1)
(63049, 90, 9) (63049, 1)
(64836, 90, 9) (64836, 1)
(64007, 90, 9) (64007, 1)
(69858, 90, 9) (69858, 1)
(56491, 90, 9) (56491, 1)
(65359, 90, 9) (65359, 1)
(61733, 90, 9) (61733, 1)
(66320, 90, 9) (66320, 1)
(61236, 90, 9) (61236, 1)
(71305, 90, 9) (71305, 1)
(52888, 90, 9) (52888, 1)
(58160, 90, 9) (58160, 1)
(70972, 90, 9) (70972, 1)
(61987, 90, 9) (61987, 1)
(43972, 90, 

In [22]:
%%time
S = 3
lstm_K5_lbs = copy.deepcopy(lstm)
outputs_lbs, targets_lbs, loss_lbs, smape_lbs, mae_lbs, rmse_lbs = fedlbs(
    global_model = lstm_K5_lbs,
    client_train_loader = train_loader,
    test_loader = test_loader,
    label_sc = label_scalers,
    n_clients = n_clients,
    num_clients_per_round = n_clients,
    batch_size = batch_size,
    num_local_epochs = num_local_epochs,
    lr = lr,
    max_rounds = max_rounds,
    model_type = model_type,
    device = device,
    S=S
)


starting average round 0
clients:  [ 0  1  2  3  4  5  6  7  8  9 10 11 12 13 14 15 16 17 18 19 20 21 22 23
 24 25 26 27 28 29 30 31 32 33 34 35 36 37 38 39]
round 0, starting client 1/40, id: 0
Epoch [1/1], Train Loss: 0.10940780982656297
round 0, starting client 2/40, id: 1
Epoch [1/1], Train Loss: 0.09746628229816756
round 0, starting client 3/40, id: 2
Epoch [1/1], Train Loss: 0.08357943894548549
round 0, starting client 4/40, id: 3
Epoch [1/1], Train Loss: 0.08585405751478438
round 0, starting client 5/40, id: 4
Epoch [1/1], Train Loss: 0.10313151226463643
round 0, starting client 6/40, id: 5
Epoch [1/1], Train Loss: 0.09223806727677587
round 0, starting client 7/40, id: 6
Epoch [1/1], Train Loss: 0.11234541428652971
round 0, starting client 8/40, id: 7
Epoch [1/1], Train Loss: 0.09395022310738291
round 0, starting client 9/40, id: 8
Epoch [1/1], Train Loss: 0.09307089619911632
round 0, starting client 10/40, id: 9
Epoch [1/1], Train Loss: 0.08281595097354576
round 0, starting cl

In [23]:
np.save(f'metrics/fedlbs_outputs_C{n_clients}.npy', np.array(outputs_lbs, dtype=object))
np.save(f'metrics/fedlbs_targets_C{n_clients}.npy', np.array(targets_lbs, dtype=object))
np.save(f'metrics/fedlbs_loss_C{n_clients}.npy', loss_lbs)
np.save(f'metrics/fedlbs_smape_C{n_clients}.npy', smape_lbs)
np.save(f'metrics/fedlbs_mae_C{n_clients}.npy', mae_lbs)
np.save(f'metrics/fedlbs_rmse_C{n_clients}.npy', rmse_lbs)

## 50

In [24]:
n_clients=50

In [25]:
train_loader = []
test_loader = []
label_scalers = []
i=0
for _, df in dataframes.items():
    if i==n_clients:
        break
    inputs_cols_indices = range(0, df.shape[1])  # use (total_demand,Year,Month,Day,Hour,Minute) columns as features
    #move the window
    inputs, labels = move_sliding_window(
        df.values,
        window_size,
        inputs_cols_indices=inputs_cols_indices,
        label_col_index=label_col_index
    )

    # Normalize the input data columns
    sc = MinMaxScaler()
    # Obtaining the scaler for the labels(usage data) so that output can be re-scaled to actual value during evaluation
    label_sc = MinMaxScaler()

    # Split data into train/test portions and combining all data into a single array
    test_portion = int(0.2 * len(inputs))

    train_x = sc.fit_transform(inputs[:-test_portion].reshape(-1, window_size * df.shape[1]))
    train_x = train_x.reshape(-1, window_size, df.shape[1])
    train_y = label_sc.fit_transform(labels[:-test_portion])

    test_x = sc.transform(inputs[-test_portion:].reshape(-1, window_size * df.shape[1]))
    test_x = test_x.reshape(-1, window_size, df.shape[1])
    test_y = label_sc.transform(labels[-test_portion:])

    # test_x.append(testx)
    # test_y.append(testy)
    label_scalers.append(label_sc)

    # pytorch data loaders
    train_data = TensorDataset(torch.from_numpy(train_x).to('cpu'), torch.from_numpy(train_y).to('cpu'))
    train_loader.append(DataLoader(train_data, batch_size=batch_size, drop_last=True))# Drop the last incomplete batch
    test_data = TensorDataset(torch.from_numpy(test_x).to('cpu'), torch.from_numpy(test_y).to('cpu'))
    test_loader.append(DataLoader(test_data, batch_size=batch_size))# Drop the last incomplete batch

    # release some memory
    del train_x, train_y
    i=i+1


(68093, 90, 9) (68093, 1)
(58528, 90, 9) (58528, 1)
(46750, 90, 9) (46750, 1)
(65300, 90, 9) (65300, 1)
(57086, 90, 9) (57086, 1)
(51617, 90, 9) (51617, 1)
(47363, 90, 9) (47363, 1)
(68901, 90, 9) (68901, 1)
(67168, 90, 9) (67168, 1)
(69578, 90, 9) (69578, 1)
(62003, 90, 9) (62003, 1)
(49050, 90, 9) (49050, 1)
(61853, 90, 9) (61853, 1)
(69521, 90, 9) (69521, 1)
(67302, 90, 9) (67302, 1)
(72217, 90, 9) (72217, 1)
(46055, 90, 9) (46055, 1)
(57157, 90, 9) (57157, 1)
(64807, 90, 9) (64807, 1)
(66845, 90, 9) (66845, 1)
(61800, 90, 9) (61800, 1)
(55024, 90, 9) (55024, 1)
(65910, 90, 9) (65910, 1)
(49996, 90, 9) (49996, 1)
(63049, 90, 9) (63049, 1)
(64836, 90, 9) (64836, 1)
(64007, 90, 9) (64007, 1)
(69858, 90, 9) (69858, 1)
(56491, 90, 9) (56491, 1)
(65359, 90, 9) (65359, 1)
(61733, 90, 9) (61733, 1)
(66320, 90, 9) (66320, 1)
(61236, 90, 9) (61236, 1)
(71305, 90, 9) (71305, 1)
(52888, 90, 9) (52888, 1)
(58160, 90, 9) (58160, 1)
(70972, 90, 9) (70972, 1)
(61987, 90, 9) (61987, 1)
(43972, 90, 

In [26]:
%%time
S = 3
lstm_K5_lbs = copy.deepcopy(lstm)
outputs_lbs, targets_lbs, loss_lbs, smape_lbs, mae_lbs, rmse_lbs = fedlbs(
    global_model = lstm_K5_lbs,
    client_train_loader = train_loader,
    test_loader = test_loader,
    label_sc = label_scalers,
    n_clients = n_clients,
    num_clients_per_round = n_clients,
    batch_size = batch_size,
    num_local_epochs = num_local_epochs,
    lr = lr,
    max_rounds = max_rounds,
    model_type = model_type,
    device = device,
    S=S
)


starting average round 0
clients:  [ 0  1  2  3  4  5  6  7  8  9 10 11 12 13 14 15 16 17 18 19 20 21 22 23
 24 25 26 27 28 29 30 31 32 33 34 35 36 37 38 39 40 41 42 43 44 45 46 47
 48 49]
round 0, starting client 1/50, id: 0
Epoch [1/1], Train Loss: 0.10940780982656297
round 0, starting client 2/50, id: 1
Epoch [1/1], Train Loss: 0.09746628229816756
round 0, starting client 3/50, id: 2
Epoch [1/1], Train Loss: 0.08357943894548549
round 0, starting client 4/50, id: 3
Epoch [1/1], Train Loss: 0.08585405751478438
round 0, starting client 5/50, id: 4
Epoch [1/1], Train Loss: 0.10313151226463643
round 0, starting client 6/50, id: 5
Epoch [1/1], Train Loss: 0.09223806727677587
round 0, starting client 7/50, id: 6
Epoch [1/1], Train Loss: 0.11234541428652971
round 0, starting client 8/50, id: 7
Epoch [1/1], Train Loss: 0.09395022310738291
round 0, starting client 9/50, id: 8
Epoch [1/1], Train Loss: 0.09307089619911632
round 0, starting client 10/50, id: 9
Epoch [1/1], Train Loss: 0.0828159

In [27]:
np.save(f'metrics/fedlbs_outputs_C{n_clients}.npy', np.array(outputs_lbs, dtype=object))
np.save(f'metrics/fedlbs_targets_C{n_clients}.npy', np.array(targets_lbs, dtype=object))
np.save(f'metrics/fedlbs_loss_C{n_clients}.npy', loss_lbs)
np.save(f'metrics/fedlbs_smape_C{n_clients}.npy', smape_lbs)
np.save(f'metrics/fedlbs_mae_C{n_clients}.npy', mae_lbs)
np.save(f'metrics/fedlbs_rmse_C{n_clients}.npy', rmse_lbs)

## 60

In [28]:
n_clients=60

In [29]:
train_loader = []
test_loader = []
label_scalers = []
i=0
for _, df in dataframes.items():
    if i==n_clients:
        break
    inputs_cols_indices = range(0, df.shape[1])  # use (total_demand,Year,Month,Day,Hour,Minute) columns as features
    #move the window
    inputs, labels = move_sliding_window(
        df.values,
        window_size,
        inputs_cols_indices=inputs_cols_indices,
        label_col_index=label_col_index
    )

    # Normalize the input data columns
    sc = MinMaxScaler()
    # Obtaining the scaler for the labels(usage data) so that output can be re-scaled to actual value during evaluation
    label_sc = MinMaxScaler()

    # Split data into train/test portions and combining all data into a single array
    test_portion = int(0.2 * len(inputs))

    train_x = sc.fit_transform(inputs[:-test_portion].reshape(-1, window_size * df.shape[1]))
    train_x = train_x.reshape(-1, window_size, df.shape[1])
    train_y = label_sc.fit_transform(labels[:-test_portion])

    test_x = sc.transform(inputs[-test_portion:].reshape(-1, window_size * df.shape[1]))
    test_x = test_x.reshape(-1, window_size, df.shape[1])
    test_y = label_sc.transform(labels[-test_portion:])

    # test_x.append(testx)
    # test_y.append(testy)
    label_scalers.append(label_sc)

    # pytorch data loaders
    train_data = TensorDataset(torch.from_numpy(train_x).to('cpu'), torch.from_numpy(train_y).to('cpu'))
    train_loader.append(DataLoader(train_data, batch_size=batch_size, drop_last=True))# Drop the last incomplete batch
    test_data = TensorDataset(torch.from_numpy(test_x).to('cpu'), torch.from_numpy(test_y).to('cpu'))
    test_loader.append(DataLoader(test_data, batch_size=batch_size))# Drop the last incomplete batch

    # release some memory
    del train_x, train_y
    i=i+1


(68093, 90, 9) (68093, 1)
(58528, 90, 9) (58528, 1)
(46750, 90, 9) (46750, 1)
(65300, 90, 9) (65300, 1)
(57086, 90, 9) (57086, 1)
(51617, 90, 9) (51617, 1)
(47363, 90, 9) (47363, 1)
(68901, 90, 9) (68901, 1)
(67168, 90, 9) (67168, 1)
(69578, 90, 9) (69578, 1)
(62003, 90, 9) (62003, 1)
(49050, 90, 9) (49050, 1)
(61853, 90, 9) (61853, 1)
(69521, 90, 9) (69521, 1)
(67302, 90, 9) (67302, 1)
(72217, 90, 9) (72217, 1)
(46055, 90, 9) (46055, 1)
(57157, 90, 9) (57157, 1)
(64807, 90, 9) (64807, 1)
(66845, 90, 9) (66845, 1)
(61800, 90, 9) (61800, 1)
(55024, 90, 9) (55024, 1)
(65910, 90, 9) (65910, 1)
(49996, 90, 9) (49996, 1)
(63049, 90, 9) (63049, 1)
(64836, 90, 9) (64836, 1)
(64007, 90, 9) (64007, 1)
(69858, 90, 9) (69858, 1)
(56491, 90, 9) (56491, 1)
(65359, 90, 9) (65359, 1)
(61733, 90, 9) (61733, 1)
(66320, 90, 9) (66320, 1)
(61236, 90, 9) (61236, 1)
(71305, 90, 9) (71305, 1)
(52888, 90, 9) (52888, 1)
(58160, 90, 9) (58160, 1)
(70972, 90, 9) (70972, 1)
(61987, 90, 9) (61987, 1)
(43972, 90, 

In [30]:
%%time
S = 3
lstm_K5_lbs = copy.deepcopy(lstm)
outputs_lbs, targets_lbs, loss_lbs, smape_lbs, mae_lbs, rmse_lbs = fedlbs(
    global_model = lstm_K5_lbs,
    client_train_loader = train_loader,
    test_loader = test_loader,
    label_sc = label_scalers,
    n_clients = n_clients,
    num_clients_per_round = n_clients,
    batch_size = batch_size,
    num_local_epochs = num_local_epochs,
    lr = lr,
    max_rounds = max_rounds,
    model_type = model_type,
    device = device,
    S=S
)


starting average round 0
clients:  [ 0  1  2  3  4  5  6  7  8  9 10 11 12 13 14 15 16 17 18 19 20 21 22 23
 24 25 26 27 28 29 30 31 32 33 34 35 36 37 38 39 40 41 42 43 44 45 46 47
 48 49 50 51 52 53 54 55 56 57 58 59]
round 0, starting client 1/60, id: 0
Epoch [1/1], Train Loss: 0.10940780982656297
round 0, starting client 2/60, id: 1
Epoch [1/1], Train Loss: 0.09746628229816756
round 0, starting client 3/60, id: 2
Epoch [1/1], Train Loss: 0.08357943894548549
round 0, starting client 4/60, id: 3
Epoch [1/1], Train Loss: 0.08585405751478438
round 0, starting client 5/60, id: 4
Epoch [1/1], Train Loss: 0.10313151226463643
round 0, starting client 6/60, id: 5
Epoch [1/1], Train Loss: 0.09223806727677587
round 0, starting client 7/60, id: 6
Epoch [1/1], Train Loss: 0.11234541428652971
round 0, starting client 8/60, id: 7
Epoch [1/1], Train Loss: 0.09395022310738291
round 0, starting client 9/60, id: 8
Epoch [1/1], Train Loss: 0.09307089619911632
round 0, starting client 10/60, id: 9
Epoc

In [31]:
np.save(f'metrics/fedlbs_outputs_C{n_clients}.npy', np.array(outputs_lbs, dtype=object))
np.save(f'metrics/fedlbs_targets_C{n_clients}.npy', np.array(targets_lbs, dtype=object))
np.save(f'metrics/fedlbs_loss_C{n_clients}.npy', loss_lbs)
np.save(f'metrics/fedlbs_smape_C{n_clients}.npy', smape_lbs)
np.save(f'metrics/fedlbs_mae_C{n_clients}.npy', mae_lbs)
np.save(f'metrics/fedlbs_rmse_C{n_clients}.npy', rmse_lbs)

## 70

In [32]:
n_clients=70

In [33]:
train_loader = []
test_loader = []
label_scalers = []
i=0
for _, df in dataframes.items():
    if i==n_clients:
        break
    inputs_cols_indices = range(0, df.shape[1])  # use (total_demand,Year,Month,Day,Hour,Minute) columns as features
    #move the window
    inputs, labels = move_sliding_window(
        df.values,
        window_size,
        inputs_cols_indices=inputs_cols_indices,
        label_col_index=label_col_index
    )

    # Normalize the input data columns
    sc = MinMaxScaler()
    # Obtaining the scaler for the labels(usage data) so that output can be re-scaled to actual value during evaluation
    label_sc = MinMaxScaler()

    # Split data into train/test portions and combining all data into a single array
    test_portion = int(0.2 * len(inputs))

    train_x = sc.fit_transform(inputs[:-test_portion].reshape(-1, window_size * df.shape[1]))
    train_x = train_x.reshape(-1, window_size, df.shape[1])
    train_y = label_sc.fit_transform(labels[:-test_portion])

    test_x = sc.transform(inputs[-test_portion:].reshape(-1, window_size * df.shape[1]))
    test_x = test_x.reshape(-1, window_size, df.shape[1])
    test_y = label_sc.transform(labels[-test_portion:])

    # test_x.append(testx)
    # test_y.append(testy)
    label_scalers.append(label_sc)

    # pytorch data loaders
    train_data = TensorDataset(torch.from_numpy(train_x).to('cpu'), torch.from_numpy(train_y).to('cpu'))
    train_loader.append(DataLoader(train_data, batch_size=batch_size, drop_last=True))# Drop the last incomplete batch
    test_data = TensorDataset(torch.from_numpy(test_x).to('cpu'), torch.from_numpy(test_y).to('cpu'))
    test_loader.append(DataLoader(test_data, batch_size=batch_size))# Drop the last incomplete batch

    # release some memory
    del train_x, train_y
    i=i+1


(68093, 90, 9) (68093, 1)
(58528, 90, 9) (58528, 1)
(46750, 90, 9) (46750, 1)
(65300, 90, 9) (65300, 1)
(57086, 90, 9) (57086, 1)
(51617, 90, 9) (51617, 1)
(47363, 90, 9) (47363, 1)
(68901, 90, 9) (68901, 1)
(67168, 90, 9) (67168, 1)
(69578, 90, 9) (69578, 1)
(62003, 90, 9) (62003, 1)
(49050, 90, 9) (49050, 1)
(61853, 90, 9) (61853, 1)
(69521, 90, 9) (69521, 1)
(67302, 90, 9) (67302, 1)
(72217, 90, 9) (72217, 1)
(46055, 90, 9) (46055, 1)
(57157, 90, 9) (57157, 1)
(64807, 90, 9) (64807, 1)
(66845, 90, 9) (66845, 1)
(61800, 90, 9) (61800, 1)
(55024, 90, 9) (55024, 1)
(65910, 90, 9) (65910, 1)
(49996, 90, 9) (49996, 1)
(63049, 90, 9) (63049, 1)
(64836, 90, 9) (64836, 1)
(64007, 90, 9) (64007, 1)
(69858, 90, 9) (69858, 1)
(56491, 90, 9) (56491, 1)
(65359, 90, 9) (65359, 1)
(61733, 90, 9) (61733, 1)
(66320, 90, 9) (66320, 1)
(61236, 90, 9) (61236, 1)
(71305, 90, 9) (71305, 1)
(52888, 90, 9) (52888, 1)
(58160, 90, 9) (58160, 1)
(70972, 90, 9) (70972, 1)
(61987, 90, 9) (61987, 1)
(43972, 90, 

In [34]:
%%time
S = 3
lstm_K5_lbs = copy.deepcopy(lstm)
outputs_lbs, targets_lbs, loss_lbs, smape_lbs, mae_lbs, rmse_lbs = fedlbs(
    global_model = lstm_K5_lbs,
    client_train_loader = train_loader,
    test_loader = test_loader,
    label_sc = label_scalers,
    n_clients = n_clients,
    num_clients_per_round = n_clients,
    batch_size = batch_size,
    num_local_epochs = num_local_epochs,
    lr = lr,
    max_rounds = max_rounds,
    model_type = model_type,
    device = device,
    S=S
)


starting average round 0
clients:  [ 0  1  2  3  4  5  6  7  8  9 10 11 12 13 14 15 16 17 18 19 20 21 22 23
 24 25 26 27 28 29 30 31 32 33 34 35 36 37 38 39 40 41 42 43 44 45 46 47
 48 49 50 51 52 53 54 55 56 57 58 59 60 61 62 63 64 65 66 67 68 69]
round 0, starting client 1/70, id: 0
Epoch [1/1], Train Loss: 0.10940780982656297
round 0, starting client 2/70, id: 1
Epoch [1/1], Train Loss: 0.09746628229816756
round 0, starting client 3/70, id: 2
Epoch [1/1], Train Loss: 0.08357943894548549
round 0, starting client 4/70, id: 3
Epoch [1/1], Train Loss: 0.08585405751478438
round 0, starting client 5/70, id: 4
Epoch [1/1], Train Loss: 0.10313151226463643
round 0, starting client 6/70, id: 5
Epoch [1/1], Train Loss: 0.09223806727677587
round 0, starting client 7/70, id: 6
Epoch [1/1], Train Loss: 0.11234541428652971
round 0, starting client 8/70, id: 7
Epoch [1/1], Train Loss: 0.09395022310738291
round 0, starting client 9/70, id: 8
Epoch [1/1], Train Loss: 0.09307089619911632
round 0, sta

In [35]:
np.save(f'metrics/fedlbs_outputs_C{n_clients}.npy', np.array(outputs_lbs, dtype=object))
np.save(f'metrics/fedlbs_targets_C{n_clients}.npy', np.array(targets_lbs, dtype=object))
np.save(f'metrics/fedlbs_loss_C{n_clients}.npy', loss_lbs)
np.save(f'metrics/fedlbs_smape_C{n_clients}.npy', smape_lbs)
np.save(f'metrics/fedlbs_mae_C{n_clients}.npy', mae_lbs)
np.save(f'metrics/fedlbs_rmse_C{n_clients}.npy', rmse_lbs)

## 80

In [36]:
n_clients=80

In [37]:
train_loader = []
test_loader = []
label_scalers = []
i=0
for _, df in dataframes.items():
    if i==n_clients:
        break
    inputs_cols_indices = range(0, df.shape[1])  # use (total_demand,Year,Month,Day,Hour,Minute) columns as features
    #move the window
    inputs, labels = move_sliding_window(
        df.values,
        window_size,
        inputs_cols_indices=inputs_cols_indices,
        label_col_index=label_col_index
    )

    # Normalize the input data columns
    sc = MinMaxScaler()
    # Obtaining the scaler for the labels(usage data) so that output can be re-scaled to actual value during evaluation
    label_sc = MinMaxScaler()

    # Split data into train/test portions and combining all data into a single array
    test_portion = int(0.2 * len(inputs))

    train_x = sc.fit_transform(inputs[:-test_portion].reshape(-1, window_size * df.shape[1]))
    train_x = train_x.reshape(-1, window_size, df.shape[1])
    train_y = label_sc.fit_transform(labels[:-test_portion])

    test_x = sc.transform(inputs[-test_portion:].reshape(-1, window_size * df.shape[1]))
    test_x = test_x.reshape(-1, window_size, df.shape[1])
    test_y = label_sc.transform(labels[-test_portion:])

    # test_x.append(testx)
    # test_y.append(testy)
    label_scalers.append(label_sc)

    # pytorch data loaders
    train_data = TensorDataset(torch.from_numpy(train_x).to('cpu'), torch.from_numpy(train_y).to('cpu'))
    train_loader.append(DataLoader(train_data, batch_size=batch_size, drop_last=True))# Drop the last incomplete batch
    test_data = TensorDataset(torch.from_numpy(test_x).to('cpu'), torch.from_numpy(test_y).to('cpu'))
    test_loader.append(DataLoader(test_data, batch_size=batch_size))# Drop the last incomplete batch

    # release some memory
    del train_x, train_y
    i=i+1


(68093, 90, 9) (68093, 1)
(58528, 90, 9) (58528, 1)
(46750, 90, 9) (46750, 1)
(65300, 90, 9) (65300, 1)
(57086, 90, 9) (57086, 1)
(51617, 90, 9) (51617, 1)
(47363, 90, 9) (47363, 1)
(68901, 90, 9) (68901, 1)
(67168, 90, 9) (67168, 1)
(69578, 90, 9) (69578, 1)
(62003, 90, 9) (62003, 1)
(49050, 90, 9) (49050, 1)
(61853, 90, 9) (61853, 1)
(69521, 90, 9) (69521, 1)
(67302, 90, 9) (67302, 1)
(72217, 90, 9) (72217, 1)
(46055, 90, 9) (46055, 1)
(57157, 90, 9) (57157, 1)
(64807, 90, 9) (64807, 1)
(66845, 90, 9) (66845, 1)
(61800, 90, 9) (61800, 1)
(55024, 90, 9) (55024, 1)
(65910, 90, 9) (65910, 1)
(49996, 90, 9) (49996, 1)
(63049, 90, 9) (63049, 1)
(64836, 90, 9) (64836, 1)
(64007, 90, 9) (64007, 1)
(69858, 90, 9) (69858, 1)
(56491, 90, 9) (56491, 1)
(65359, 90, 9) (65359, 1)
(61733, 90, 9) (61733, 1)
(66320, 90, 9) (66320, 1)
(61236, 90, 9) (61236, 1)
(71305, 90, 9) (71305, 1)
(52888, 90, 9) (52888, 1)
(58160, 90, 9) (58160, 1)
(70972, 90, 9) (70972, 1)
(61987, 90, 9) (61987, 1)
(43972, 90, 

In [38]:
%%time
S = 3
lstm_K5_lbs = copy.deepcopy(lstm)
outputs_lbs, targets_lbs, loss_lbs, smape_lbs, mae_lbs, rmse_lbs = fedlbs(
    global_model = lstm_K5_lbs,
    client_train_loader = train_loader,
    test_loader = test_loader,
    label_sc = label_scalers,
    n_clients = n_clients,
    num_clients_per_round = n_clients,
    batch_size = batch_size,
    num_local_epochs = num_local_epochs,
    lr = lr,
    max_rounds = max_rounds,
    model_type = model_type,
    device = device,
    S=S
)


starting average round 0
clients:  [ 0  1  2  3  4  5  6  7  8  9 10 11 12 13 14 15 16 17 18 19 20 21 22 23
 24 25 26 27 28 29 30 31 32 33 34 35 36 37 38 39 40 41 42 43 44 45 46 47
 48 49 50 51 52 53 54 55 56 57 58 59 60 61 62 63 64 65 66 67 68 69 70 71
 72 73 74 75 76 77 78 79]
round 0, starting client 1/80, id: 0
Epoch [1/1], Train Loss: 0.10940780982656297
round 0, starting client 2/80, id: 1
Epoch [1/1], Train Loss: 0.09746628229816756
round 0, starting client 3/80, id: 2
Epoch [1/1], Train Loss: 0.08357943894548549
round 0, starting client 4/80, id: 3
Epoch [1/1], Train Loss: 0.08585405751478438
round 0, starting client 5/80, id: 4
Epoch [1/1], Train Loss: 0.10313151226463643
round 0, starting client 6/80, id: 5
Epoch [1/1], Train Loss: 0.09223806727677587
round 0, starting client 7/80, id: 6
Epoch [1/1], Train Loss: 0.11234541428652971
round 0, starting client 8/80, id: 7
Epoch [1/1], Train Loss: 0.09395022310738291
round 0, starting client 9/80, id: 8
Epoch [1/1], Train Loss: 0

In [39]:
np.save(f'metrics/fedlbs_outputs_C{n_clients}.npy', np.array(outputs_lbs, dtype=object))
np.save(f'metrics/fedlbs_targets_C{n_clients}.npy', np.array(targets_lbs, dtype=object))
np.save(f'metrics/fedlbs_loss_C{n_clients}.npy', loss_lbs)
np.save(f'metrics/fedlbs_smape_C{n_clients}.npy', smape_lbs)
np.save(f'metrics/fedlbs_mae_C{n_clients}.npy', mae_lbs)
np.save(f'metrics/fedlbs_rmse_C{n_clients}.npy', rmse_lbs)

## 90

In [40]:
n_clients=90

In [41]:
train_loader = []
test_loader = []
label_scalers = []
i=0
for _, df in dataframes.items():
    if i==n_clients:
        break
    inputs_cols_indices = range(0, df.shape[1])  # use (total_demand,Year,Month,Day,Hour,Minute) columns as features
    #move the window
    inputs, labels = move_sliding_window(
        df.values,
        window_size,
        inputs_cols_indices=inputs_cols_indices,
        label_col_index=label_col_index
    )

    # Normalize the input data columns
    sc = MinMaxScaler()
    # Obtaining the scaler for the labels(usage data) so that output can be re-scaled to actual value during evaluation
    label_sc = MinMaxScaler()

    # Split data into train/test portions and combining all data into a single array
    test_portion = int(0.2 * len(inputs))

    train_x = sc.fit_transform(inputs[:-test_portion].reshape(-1, window_size * df.shape[1]))
    train_x = train_x.reshape(-1, window_size, df.shape[1])
    train_y = label_sc.fit_transform(labels[:-test_portion])

    test_x = sc.transform(inputs[-test_portion:].reshape(-1, window_size * df.shape[1]))
    test_x = test_x.reshape(-1, window_size, df.shape[1])
    test_y = label_sc.transform(labels[-test_portion:])

    # test_x.append(testx)
    # test_y.append(testy)
    label_scalers.append(label_sc)

    # pytorch data loaders
    train_data = TensorDataset(torch.from_numpy(train_x).to('cpu'), torch.from_numpy(train_y).to('cpu'))
    train_loader.append(DataLoader(train_data, batch_size=batch_size, drop_last=True))# Drop the last incomplete batch
    test_data = TensorDataset(torch.from_numpy(test_x).to('cpu'), torch.from_numpy(test_y).to('cpu'))
    test_loader.append(DataLoader(test_data, batch_size=batch_size))# Drop the last incomplete batch

    # release some memory
    del train_x, train_y
    i=i+1


(68093, 90, 9) (68093, 1)
(58528, 90, 9) (58528, 1)
(46750, 90, 9) (46750, 1)
(65300, 90, 9) (65300, 1)
(57086, 90, 9) (57086, 1)
(51617, 90, 9) (51617, 1)
(47363, 90, 9) (47363, 1)
(68901, 90, 9) (68901, 1)
(67168, 90, 9) (67168, 1)
(69578, 90, 9) (69578, 1)
(62003, 90, 9) (62003, 1)
(49050, 90, 9) (49050, 1)
(61853, 90, 9) (61853, 1)
(69521, 90, 9) (69521, 1)
(67302, 90, 9) (67302, 1)
(72217, 90, 9) (72217, 1)
(46055, 90, 9) (46055, 1)
(57157, 90, 9) (57157, 1)
(64807, 90, 9) (64807, 1)
(66845, 90, 9) (66845, 1)
(61800, 90, 9) (61800, 1)
(55024, 90, 9) (55024, 1)
(65910, 90, 9) (65910, 1)
(49996, 90, 9) (49996, 1)
(63049, 90, 9) (63049, 1)
(64836, 90, 9) (64836, 1)
(64007, 90, 9) (64007, 1)
(69858, 90, 9) (69858, 1)
(56491, 90, 9) (56491, 1)
(65359, 90, 9) (65359, 1)
(61733, 90, 9) (61733, 1)
(66320, 90, 9) (66320, 1)
(61236, 90, 9) (61236, 1)
(71305, 90, 9) (71305, 1)
(52888, 90, 9) (52888, 1)
(58160, 90, 9) (58160, 1)
(70972, 90, 9) (70972, 1)
(61987, 90, 9) (61987, 1)
(43972, 90, 

In [42]:
%%time
S = 3
lstm_K5_lbs = copy.deepcopy(lstm)
outputs_lbs, targets_lbs, loss_lbs, smape_lbs, mae_lbs, rmse_lbs = fedlbs(
    global_model = lstm_K5_lbs,
    client_train_loader = train_loader,
    test_loader = test_loader,
    label_sc = label_scalers,
    n_clients = n_clients,
    num_clients_per_round = n_clients,
    batch_size = batch_size,
    num_local_epochs = num_local_epochs,
    lr = lr,
    max_rounds = max_rounds,
    model_type = model_type,
    device = device,
    S=S
)


starting average round 0
clients:  [ 0  1  2  3  4  5  6  7  8  9 10 11 12 13 14 15 16 17 18 19 20 21 22 23
 24 25 26 27 28 29 30 31 32 33 34 35 36 37 38 39 40 41 42 43 44 45 46 47
 48 49 50 51 52 53 54 55 56 57 58 59 60 61 62 63 64 65 66 67 68 69 70 71
 72 73 74 75 76 77 78 79 80 81 82 83 84 85 86 87 88 89]
round 0, starting client 1/90, id: 0
Epoch [1/1], Train Loss: 0.10940780982656297
round 0, starting client 2/90, id: 1
Epoch [1/1], Train Loss: 0.09746628229816756
round 0, starting client 3/90, id: 2
Epoch [1/1], Train Loss: 0.08357943894548549
round 0, starting client 4/90, id: 3
Epoch [1/1], Train Loss: 0.08585405751478438
round 0, starting client 5/90, id: 4
Epoch [1/1], Train Loss: 0.10313151226463643
round 0, starting client 6/90, id: 5
Epoch [1/1], Train Loss: 0.09223806727677587
round 0, starting client 7/90, id: 6
Epoch [1/1], Train Loss: 0.11234541428652971
round 0, starting client 8/90, id: 7
Epoch [1/1], Train Loss: 0.09395022310738291
round 0, starting client 9/90, id

In [43]:
np.save(f'metrics/fedlbs_outputs_C{n_clients}.npy', np.array(outputs_lbs, dtype=object))
np.save(f'metrics/fedlbs_targets_C{n_clients}.npy', np.array(targets_lbs, dtype=object))
np.save(f'metrics/fedlbs_loss_C{n_clients}.npy', loss_lbs)
np.save(f'metrics/fedlbs_smape_C{n_clients}.npy', smape_lbs)
np.save(f'metrics/fedlbs_mae_C{n_clients}.npy', mae_lbs)
np.save(f'metrics/fedlbs_rmse_C{n_clients}.npy', rmse_lbs)